In [1]:
import numpy as np
import pandas as pd
import ast
from matplotlib import pyplot as plt
import seaborn as sns
from sklearn.decomposition import PCA
from sklearn.metrics import confusion_matrix, accuracy_score, classification_report, f1_score, precision_score, recall_score, roc_auc_score, roc_curve
from sklearn.model_selection import train_test_split, KFold
from sklearn.linear_model import LogisticRegression
from sklearn.preprocessing import StandardScaler
from sklearn.ensemble import RandomForestClassifier
from imblearn.over_sampling import SMOTE
from sklearn.model_selection import cross_val_score
from sklearn.neighbors import KNeighborsClassifier
from sklearn.model_selection import GridSearchCV
from sklearn.cluster import KMeans
%matplotlib inline
from sklearn.feature_selection import RFE
from sklearn.feature_selection import RFE
from sklearn.linear_model import LogisticRegression, Lasso
import numpy as np
from sklearn.neural_network import MLPClassifier
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler
from sklearn.metrics import classification_report
import pandas as pd
from sklearn.multiclass import OneVsRestClassifier

In [2]:
df = pd.read_csv('Final_project_finished_Continents.csv')  # index=False avoids saving row indices

In [3]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 18608 entries, 0 to 18607
Data columns (total 98 columns):
 #   Column                        Non-Null Count  Dtype  
---  ------                        --------------  -----  
 0   Unnamed: 0.1                  18608 non-null  int64  
 1   Unnamed: 0                    18608 non-null  int64  
 2   player_id                     18608 non-null  int64  
 3   name                          18608 non-null  object 
 4   full_name                     18608 non-null  object 
 5   height_cm                     18608 non-null  int64  
 6   weight_kg                     18608 non-null  int64  
 7   dob                           18608 non-null  object 
 8   positions                     18608 non-null  object 
 9   preferred_foot                18608 non-null  object 
 10  body_type                     18608 non-null  object 
 11  club_id                       18608 non-null  int64  
 12  club_name                     18608 non-null  object 
 13  c

In [4]:
print(df['league_name'].unique())

['Primeira Liga (POR 1) [Portugal]' 'League Two (ENG 4) [England]'
 'Pro League (SAU 1) [Saudi Arabia]' 'Allsvenskan (SWE 1) [Sweden]'
 'La Liga (ESP 1) [Spain]' 'Primera División (PAR 1) [Paraguay]'
 'Ligue 1 (FRA 1) [France]' 'Premiership (SP 1) [Scotland]'
 'Liga Pro (ECU 1) [Ecuador]'
 'División de Fútbol Profesional (BOL 1) [Bolivia]'
 'Primera División (URY 1) [Uruguay]' 'Eliteserien (NOR 1) [Norway]'
 'Liga Profesional de Fútbol (ARG 1) [Argentina]'
 'Major League Soccer (MLS 1) [USA]' '2. Bundesliga (GER 2) [Germany]'
 'Bundesliga (GER 1) [Germany]' 'Primera Division (VEN 1) [Venezuela]'
 'Eredivisie (NED 1) [Netherlands]' 'Süper Lig (TUR 1) [Turkey]'
 'Ligue 2 (FRA 2) [France]' 'Championship (ENG 2) [England]'
 'La Liga 2 (ESP 2) [Spain]' 'Premier League (ENG 1) [England]'
 'Serie A (ITA 1) [Italy]' 'A-League Men (AUS 1) [Australia]'
 'Serie B (ITA 2) [Italy]' 'Pro League (BEL 1) [Belgium]'
 'Superliga (DEN 1) [Denmark]' 'Super League (SWI 1) [Switzerland]'
 'Liga I (ROM 1) [R

In [5]:
unique_leagues_id = df['league_name_id'].unique()
unique_leagues_id

unique_leagues = df['league_name'].unique()
unique_leagues

array(['Primeira Liga (POR 1) [Portugal]', 'League Two (ENG 4) [England]',
       'Pro League (SAU 1) [Saudi Arabia]',
       'Allsvenskan (SWE 1) [Sweden]', 'La Liga (ESP 1) [Spain]',
       'Primera División (PAR 1) [Paraguay]', 'Ligue 1 (FRA 1) [France]',
       'Premiership (SP 1) [Scotland]', 'Liga Pro (ECU 1) [Ecuador]',
       'División de Fútbol Profesional (BOL 1) [Bolivia]',
       'Primera División (URY 1) [Uruguay]',
       'Eliteserien (NOR 1) [Norway]',
       'Liga Profesional de Fútbol (ARG 1) [Argentina]',
       'Major League Soccer (MLS 1) [USA]',
       '2. Bundesliga (GER 2) [Germany]', 'Bundesliga (GER 1) [Germany]',
       'Primera Division (VEN 1) [Venezuela]',
       'Eredivisie (NED 1) [Netherlands]', 'Süper Lig (TUR 1) [Turkey]',
       'Ligue 2 (FRA 2) [France]', 'Championship (ENG 2) [England]',
       'La Liga 2 (ESP 2) [Spain]', 'Premier League (ENG 1) [England]',
       'Serie A (ITA 1) [Italy]', 'A-League Men (AUS 1) [Australia]',
       'Serie B (ITA 2

## Converting the league names into a smaller unique identifier, for use in flask app routes

In [6]:
def get_league_name_id(league_name_string):
    if "(" in league_name_string:
        league_name_id = league_name_string.split('(')[1].split(')')[0].strip()

        league_name_id = league_name_id.lower()
        league_name_id = league_name_id.replace(' ', '')

        return league_name_id


df['league_name_id'] = df['league_name'].apply(get_league_name_id)

print(df[['league_name', 'league_name_id']])


                              league_name league_name_id
0        Primeira Liga (POR 1) [Portugal]           por1
1            League Two (ENG 4) [England]           eng4
2       Pro League (SAU 1) [Saudi Arabia]           sau1
3            Allsvenskan (SWE 1) [Sweden]           swe1
4                 La Liga (ESP 1) [Spain]           esp1
...                                   ...            ...
18603   Major League Soccer (MLS 1) [USA]           mls1
18604  Primera División (URY 1) [Uruguay]           ury1
18605  Primera División (URY 1) [Uruguay]           ury1
18606  Primera División (URY 1) [Uruguay]           ury1
18607     2. Bundesliga (GER 2) [Germany]           ger2

[18608 rows x 2 columns]


In [7]:
df['league_name'].value_counts()

league_name
Major League Soccer (MLS 1) [USA]                   782
Liga Profesional de Fútbol (ARG 1) [Argentina]      761
Championship (ENG 2) [England]                      702
League One (ENG 3) [England]                        658
League Two (ENG 4) [England]                        651
La Liga 2 (ESP 2) [Spain]                           635
Premier League (ENG 1) [England]                    634
La Liga (ESP 1) [Spain]                             629
Serie B (ITA 2) [Italy]                             561
Serie A (ITA 1) [Italy]                             561
3. Liga (GER 3) [Germany]                           550
Ligue 2 (FRA 2) [France]                            549
Süper Lig (TUR 1) [Turkey]                          532
Bundesliga (GER 1) [Germany]                        528
2. Bundesliga (GER 2) [Germany]                     527
Pro League (SAU 1) [Saudi Arabia]                   524
Eredivisie (NED 1) [Netherlands]                    512
Primeira Liga (POR 1) [Portugal]    

In [9]:
df['league_name_id'].value_counts()

league_name_id
mls1    782
arg1    761
eng2    702
eng3    658
eng4    651
esp2    635
eng1    634
esp1    629
ita2    561
ita1    561
ger3    550
fra2    549
tur1    532
ger1    528
ger2    527
sau1    524
ned1    512
por1    499
pol1    480
fra1    476
bel1    442
csl1    429
rom1    414
swe1    412
nor1    409
kor1    336
swi1    336
au1     327
isl1    326
den1    324
aus1    321
sp1     303
bra1    279
irl1    252
par1    238
chi1    210
ury1    200
col1    197
bol1    191
ecu1    185
ven1    177
per1    163
gre1     83
cze1     80
ukr1     56
cro1     56
uae1     28
fin1     28
hun1     28
cyp1     27
Name: count, dtype: int64

## Name of players in league

### Template: df[df['column name here'] == 'key/value in that column']['related column to get the values you want']

In [19]:
df[df['league_name'] == '1. Division (CYP 1) [Cyprus]']['name']

1040                    Tomané
1353             El Fardou Ben
1707                 Vid Belec
1803          Radosav Petrović
1849            Georgios Efrem
2055            Wilson Eduardo
2616        Dieumerci Ndongala
3849          Lucas Villafañez
4025               Mateo Sušić
4830             Issam Chebake
5472                    Dálcio
5552          Anastasios Donis
5557               Lasha Dvali
6997         Georgi Kostadinov
7332          Giorgi Kvilitaia
7708            Kingsley Sarfo
13820        Stylianos Vrontis
13859          Giannis Satsias
13871         Paris Polykarpou
14780          Stefanos Kittos
15299    Andreas Christodoulou
15446               Marquinhos
15555             David Djiama
15634           Rafael Moreira
17078          Fawaz Abdullahi
17079      Andreas Karamanolis
17520                    Jefté
Name: name, dtype: object

In [21]:
avg_age = df[df['league_name'] == 'Nemzeti Bajnokság I (HUN 1) [Hungary]']['age'].mean()
print(avg_age)

27.928571428571427


In [23]:
df[df['league_name'] == '1. Division (CYP 1) [Cyprus]']['nation_Nation'].value_counts()

nation_Nation
Cyprus                    8
Portugal                  2
Brazil                    2
Georgia                   2
Morocco                   1
Ghana                     1
Bulgaria                  1
Greece                    1
Guinea-Bissau             1
Bosnia and Herzegovina    1
Comoros                   1
Argentina                 1
Congo DR                  1
Angola                    1
Serbia                    1
Slovenia                  1
Nigeria                   1
Name: count, dtype: int64

## tips for analysis using age:

- Get average/mean age in leagues
- Get youngest player
- Get oldest player
- Get age range groups and the percentage in the groups (Keep the group age consistent across all leagues)
- Get Avg age for each position in the league
- Get oldest age for each positons in league
- Get youngest age for each positon in league
- Get the Career length of the different aged players as well, see how long they have been playing for.

### Feel free to think up and add more to make the analyssi better

# These points for age are finished now, can add more later if anything.

## TRY A HEAT MAP TO SEE IF WE CAN FIND ANY CORRELATION MAYBE

In [26]:
bins = [15, 20, 25, 30, 35, 40, 45, 50] #These are the borders for the age groupings, can change depending.
labels = ['15-20', '21-25', '26-30', '31-35', '36-40', '41-45', '46-50'] #These are the age ranges, we can make this broader or more specfici depending.
df['age_group'] = pd.cut(df['age'], bins=bins, labels=labels, right=True)



for name in unique_leagues_id:
    league_df = df[df['league_name_id'] == name]

    group_counts = league_df['age_group'].value_counts(normalize=True) * 100  # as percentage
    
    avg_age = league_df['age'].mean()
    min_age = league_df['age'].min()
    max_age = league_df['age'].max()
    max_career = league_df['league_Career_length'].max()
    min_career = league_df['league_Career_length'].min()
    avg_career = league_df['league_Career_length'].mean()
    positions = ["ST", "RWB", "RW", "RM", "RB", "LWB", "LW", "LM", "LB", "GK", "CM", "CF", "CDM", "CB", "CAM"]
    print(f'Average Age for each positions in the league: {name}')
    for pos in positions:
        pos_df = league_df[league_df[pos] == 1]

        if pos_df.empty:
            print(f'No players in this position: {pos}')
            print("\n")
        else:
            avg_age_pos = pos_df['age'].mean()
            min_age_pos = pos_df['age'].min()
            max_age_pos = pos_df['age'].max()
            max_career_pos = pos_df['league_Career_length'].max()
            min_career_pos = pos_df['league_Career_length'].min()
            avg_career_pos = pos_df['league_Career_length'].mean()

            print(f'Average age for {pos} is : {avg_age_pos:.2f} years old')
            print(f'Youngest age  for {pos} is : {min_age_pos:.2f} years old')
            print(f'Oldest age for {pos} is : {max_age_pos:.2f} years old')
            print(f'Max Career length for {pos} is : {max_career_pos:.2f} years')
            print(f'Min Career length for {pos} is : {min_career_pos:.2f} years')
            print(f'Average Career length for {pos} is : {avg_career_pos:.2f} years')
            print("\n")
        
    
    print("\n")
    print(f"Overall for the {name} League")
    print(f'Average age is : {avg_age:.2f} years old')
    print(f'Youngest age is : {min_age:.2f} years old')
    print(f'Oldest age is : {max_age:.2f} years old')
    print(f'Max Career length is : {max_career:.2f} years')
    print(f'Min Career length is : {min_career:.2f} years')
    print(f'Average Career length is : {avg_career:.2f} years')
    print(f"Age Group Distribution for League: {name}")
    print(group_counts)
    print("\n")
    print("=======================================================================")

Average Age for each positions in the league: por1
Average age for ST is : 26.07 years old
Youngest age  for ST is : 20.00 years old
Oldest age for ST is : 35.00 years old
Max Career length for ST is : 15.00 years
Min Career length for ST is : 1.00 years
Average Career length for ST is : 3.46 years


Average age for RWB is : 24.95 years old
Youngest age  for RWB is : 20.00 years old
Oldest age for RWB is : 32.00 years old
Max Career length for RWB is : 12.00 years
Min Career length for RWB is : 1.00 years
Average Career length for RWB is : 3.00 years


Average age for RW is : 26.02 years old
Youngest age  for RW is : 19.00 years old
Oldest age for RW is : 37.00 years old
Max Career length for RW is : 12.00 years
Min Career length for RW is : 1.00 years
Average Career length for RW is : 2.90 years


Average age for RM is : 26.03 years old
Youngest age  for RM is : 18.00 years old
Oldest age for RM is : 37.00 years old
Max Career length for RM is : 17.00 years
Min Career length for RM is

### Avg age

In [29]:
bins = [15, 20, 25, 30, 35, 40, 45, 50]
labels = ['15-20', '21-25', '26-30', '31-35', '36-40', '41-45', '46-50']
df['age_group'] = pd.cut(df['age'], bins=bins, labels=labels, right=True)



group_counts = df[df['league_name_id'] == 'cyp1']['age_group'].value_counts(normalize=True) * 100
avg_age = df[df['league_name_id'] == 'cyp1']['age'].mean()
min_age = df[df['league_name_id'] == 'cyp1']['age'].min()
max_age = df[df['league_name_id'] == 'cyp1']['age'].max()
max_career = df[df['league_name_id'] == 'cyp1']['league_Career_length'].max()
min_career = df[df['league_name_id'] == 'cyp1']['league_Career_length'].min()
avg_career = df[df['league_name_id'] == 'cyp1']['league_Career_length'].mean()
age_counts = df[df['league_name_id'] == 'cyp1']['age'].value_counts()
total_count = df[df['league_name_id'] == 'cyp1']['age'].count()
positions = ["ST", "RWB", "RW", "RM", "RB", "LWB", "LW", "LM", "LB", "GK", "CM", "CF", "CDM", "CB", "CAM"]
print("Average Age for each positions: ")
for pos in positions:
    avg_age_pos = df[(df['league_name_id'] == 'por1') & (df[pos] == 1)]['age'].mean()
    min_age_pos = df[(df['league_name_id'] == 'por1') & (df[pos] == 1)]['age'].min()
    max_age_pos = df[(df['league_name_id'] == 'por1') & (df[pos] == 1)]['age'].max()
    max_career_pos = df[(df['league_name_id'] == 'por1') & (df[pos] == 1)]['league_Career_length'].max()
    min_career_pos = df[(df['league_name_id'] == 'por1') & (df[pos] == 1)]['league_Career_length'].min()
    avg_career_pos = df[(df['league_name_id'] == 'por1') & (df[pos] == 1)]['league_Career_length'].mean()
    if  np.isnan(avg_age_pos) or np.isnan(min_age_pos) or np.isnan(max_age_pos) or np.isnan(max_career_pos) or np.isnan(min_career_pos) or np.isnan(avg_career_pos):
        avg_age_pos = "No players in this position!"
        print(f'{avg_age_pos} for: {pos}')
        print("\n")
    else:
        print(f'Average age for {pos} is : {avg_age_pos:.2f} years old')
        print(f'Youngest age  for {pos} is : {min_age_pos:.2f} years old')
        print(f'Oldest age for {pos} is : {max_age_pos:.2f} years old')
        print(f'Max Career length for {pos} is : {max_career_pos:.2f} years')
        print(f'Min Career length for {pos} is : {min_career_pos:.2f} years')
        print(f'Average Career length for {pos} is : {avg_career_pos:.2f} years')
        print("\n")

print("\n")
print("\n")
print(f"Age Group Distribution for League: {name}")
print(group_counts)
print("\n")
print(f'Average age is : {avg_age:.2f} years old')
print(f'Youngest age is : {min_age:.2f} years old')
print(f'Oldest age is : {max_age:.2f} years old')
print(f'Max Career length is : {max_career:.2f} years')
print(f'Min Career length is : {min_career:.2f} years')
print(f'Average Career length is : {avg_career:.2f} years')
print(f'Age counts is : {age_counts}')
print(f'total counts is : {total_count}')

Average Age for each positions: 
Average age for ST is : 26.07 years old
Youngest age  for ST is : 20.00 years old
Oldest age for ST is : 35.00 years old
Max Career length for ST is : 15.00 years
Min Career length for ST is : 1.00 years
Average Career length for ST is : 3.46 years


Average age for RWB is : 24.95 years old
Youngest age  for RWB is : 20.00 years old
Oldest age for RWB is : 32.00 years old
Max Career length for RWB is : 12.00 years
Min Career length for RWB is : 1.00 years
Average Career length for RWB is : 3.00 years


Average age for RW is : 26.02 years old
Youngest age  for RW is : 19.00 years old
Oldest age for RW is : 37.00 years old
Max Career length for RW is : 12.00 years
Min Career length for RW is : 1.00 years
Average Career length for RW is : 2.90 years


Average age for RM is : 26.03 years old
Youngest age  for RM is : 18.00 years old
Oldest age for RM is : 37.00 years old
Max Career length for RM is : 17.00 years
Min Career length for RM is : 1.00 years
Aver

## Some tips for analysis using country:

These are all per league:
- Get Number of countries/nations present in each league
- Get the Country with most amount of players (Do like a top 5 or top 10 ranking, since 1 is obviously the domestic country)
- Get the country that has the most number of players for each specific position (Tells if that league is biased towards a certain country or region for positons)
- Consider grouping the countries by regions/continents (Europe, Africa, Asia etc. and then doing the analysis with thsi as well)
- Get the distribution of countries in the league
- Do the age analysis point shere as well, but this time do it for the countiees in the league (If a country isnt in the league then its 0)
  

### Feel free to think up and add more to make the analyssi better

In [7]:
for name in unique_leagues_id:
    nation_df = df[df['league_name_id'] == name]
    print("===========================================")
    print(f'Doing analysis in this nation: {name}')

    positions = ["ST", "RWB", "RW", "RM", "RB", "LWB", "LW", "LM", "LB", "GK", "CM", "CF", "CDM", "CB", "CAM"]
    unique_nations = nation_df['nation_Nation'].unique()
    unique_nations = list(unique_nations)

    total_count = nation_df.shape[0]
    nation_count = nation_df['nation_Nation'].value_counts()

    max_nation_name = nation_count.idxmax()
    max_nation_num = nation_count.max()

    
    nation_max_by_position = {
        pos: {"count": 0, "nation": None} for pos in positions
    }

    for nation in unique_nations:
        spec_count = nation_df[nation_df['nation_Nation'] == nation].shape[0]
        percentage_count = (spec_count / total_count) * 100
        print("\n")
        print(f'The distribution of players for {nation} is: {percentage_count:.2f}%')
        print(f'The number of players in {nation} is: {spec_count}')

        for pos in positions:
            pos_df = nation_df[(nation_df[pos] == 1) & (nation_df['nation_Nation'] == nation)]
            count_pos = pos_df.shape[0]

            print(f'Number of players that are {pos} is :{count_pos} from {nation}')

            if count_pos > nation_max_by_position[pos]["count"]:
                nation_max_by_position[pos]["count"] = count_pos
                nation_max_by_position[pos]["nation"] = nation

    print("\n")
    print(f'The nation with the most players is: {max_nation_name} with {max_nation_num} players')
    print(f'The unique nations present in this league: {unique_nations}')
    print(f'The total number of players in this league, {name}: {total_count}')

    for pos in positions:
        print(
            f'The Highest number of {pos} players are from: '
            f'{nation_max_by_position[pos]["count"]} in the nation: '
            f'{nation_max_by_position[pos]["nation"]}'
        )

NameError: name 'unique_leagues_id' is not defined

In [33]:
for name in unique_leagues_id:
    nation_df = df[df['league_name_id'] == name]
    print("===========================================")
    print(f'Doing analysis in this nation: {name}')


    positions = ["ST", "RWB", "RW", "RM", "RB", "LWB", "LW", "LM", "LB", "GK", "CM", "CF", "CDM", "CB", "CAM"]
    unique_nations = nation_df['nation_Nation'].unique()
    unique_nations = list(unique_nations)
    
    total_count = nation_df.shape[0]
    nation_count = nation_df['nation_Nation'].value_counts()
    
    max_nation_name = nation_count.idxmax()
    max_nation_num = nation_count.max()
    print(f'The nation with the most players is: {max_nation_name} with {max_nation_num} players')

    nation_max_ST =0
    nation_max_RWB =0
    nation_max_RW =0
    nation_max_RM =0
    nation_max_RB =0
    nation_max_LWB =0
    nation_max_LW =0
    nation_max_LM =0
    nation_max_LB =0
    nation_max_GK =0
    nation_max_CM =0
    nation_max_CF =0
    nation_max_CDM =0
    nation_max_CB =0
    nation_max_CAM =0
    
    for nation in unique_nations:
        spec_count = nation_df[nation_df['nation_Nation'] == nation].shape[0]
        percentage_count = (spec_count / total_count) * 100
        print("\n")
        print(f'The distribution of players for {nation} is: {percentage_count:.2f}%')
        print(f'The number of players in {nation} is: {spec_count}')

        positions = ["ST", "RWB", "RW", "RM", "RB", "LWB", "LW", "LM", "LB", "GK", "CM", "CF", "CDM", "CB", "CAM"]
        
    
        for pos in positions:
            pos_df = nation_df[(nation_df[pos] == 1) & (nation_df['nation_Nation'] == nation)]
            
            count_pos = pos_df.shape[0]
            # min_age_pos = pos_df['nation_Nation'].value_counts().min()
            # max_age_pos = pos_df['nation_Nation'].max()
            
            #print(f'Number of players that are {pos} is :{count_pos:} from {nation}')


            if pos == "ST":
                if count_pos > nation_max_ST:
                    nation_max_ST = count_pos
                    nation_max_ST_name = nation

            if pos == "RWB":
                if count_pos > nation_max_RWB:
                    nation_max_RWB = count_pos
                    nation_max_RWB_name = nation

            if pos == "RW":
                if count_pos > nation_max_RW:
                    nation_max_RW = count_pos
                    nation_max_RW_name = nation

            if pos == "RM":
                if count_pos > nation_max_RM:
                    nation_max_RM = count_pos
                    nation_max_RM_name = nation

            if pos == "RB":
                if count_pos > nation_max_RB:
                    nation_max_RB = count_pos
                    nation_max_RB_name = nation

            if pos == "LWB":
                if count_pos > nation_max_LWB:
                    nation_max_LWB = count_pos
                    nation_max_LWB_name = nation

            if pos == "LW":
                if count_pos > nation_max_LW:
                    nation_max_LW = count_pos
                    nation_max_LW_name = nation

            if pos == "LM":
                if count_pos > nation_max_LM:
                    nation_max_LM = count_pos
                    nation_max_LM_name = nation

            if pos == "LB":
                if count_pos > nation_max_LB:
                    nation_max_LB = count_pos
                    nation_max_LB_name = nation

            if pos == "GK":
                if count_pos > nation_max_GK:
                    nation_max_GK = count_pos
                    nation_max_GK_name = nation

            if pos == "CF":
                if count_pos > nation_max_CF:
                    nation_max_CF = count_pos
                    nation_max_CF_name = nation

            if pos == "CM":
                if count_pos > nation_max_CM:
                    nation_max_CM = count_pos
                    nation_max_CM_name = nation

            if pos == "CDM":
                if count_pos > nation_max_CDM:
                    nation_max_CDM = count_pos
                    nation_max_CDM_name = nation

            if pos == "CB":
                if count_pos > nation_max_CB:
                    nation_max_CB = count_pos
                    nation_max_CB_name = nation

            if pos == "CAM":
                if count_pos > nation_max_CAM:
                    nation_max_CAM = count_pos
                    nation_max_CAM_name = nation

            # print(f'Youngest age  for {pos} is : {min_age_pos:.2f} years old')
            # print(f'Oldest age for {pos} is : {max_age_pos:.2f} years old')
            #print(f'We are in this nation right now: {nation}')
            #print("\n")
    
    print("\n")
    print(f'The nation with the most players is: {max_nation_name} with {max_nation_num} players')
    print(f'The unique nations present in this league: {unique_nations}')
    print(f'The total number of players in this league, {name}: {total_count}')
    print(f'The Highest number of ST players are from: {nation_max_ST} in the nation: {nation_max_ST_name}')
    print(f'The Highest number of RWB players are from: {nation_max_RWB} in the nation: {nation_max_RWB_name}')
    print(f'The Highest number of RW players are from: {nation_max_RW} in the nation: {nation_max_RW_name}')
    print(f'The Highest number of RM players are from: {nation_max_RM} in the nation: {nation_max_RM_name}')
    print(f'The Highest number of RB players are from: {nation_max_RB} in the nation: {nation_max_RB_name}')
    print(f'The Highest number of LWB players are from: {nation_max_LWB} in the nation: {nation_max_LWB_name}')
    print(f'The Highest number of LW players are from: {nation_max_LW} in the nation: {nation_max_LW_name}')
    print(f'The Highest number of LM players are from: {nation_max_LM} in the nation: {nation_max_LM_name}')
    print(f'The Highest number of LB players are from: {nation_max_LB} in the nation: {nation_max_LB_name}')
    print(f'The Highest number of GK players are from: {nation_max_GK} in the nation: {nation_max_GK_name}')
    print(f'The Highest number of CM players are from: {nation_max_CM} in the nation: {nation_max_CM_name}')
    print(f'The Highest number of CF players are from: {nation_max_CF} in the nation: {nation_max_CF_name}')
    print(f'The Highest number of CDM players are from: {nation_max_CDM} in the nation: {nation_max_CDM_name}')
    print(f'The Highest number of CB players are from: {nation_max_CB} in the nation: {nation_max_CB_name}')
    print(f'The Highest number of CAM players are from: {nation_max_CAM} in the nation: {nation_max_CAM_name}')

Doing analysis in this nation: por1
The nation with the most players is: Portugal with 203 players


The distribution of players for Portugal is: 40.68%
The number of players in Portugal is: 203


The distribution of players for Serbia is: 1.00%
The number of players in Serbia is: 5


The distribution of players for Brazil is: 20.24%
The number of players in Brazil is: 101


The distribution of players for France is: 2.20%
The number of players in France is: 11


The distribution of players for Netherlands is: 0.80%
The number of players in Netherlands is: 4


The distribution of players for Belarus is: 0.20%
The number of players in Belarus is: 1


The distribution of players for Equatorial Guinea is: 0.20%
The number of players in Equatorial Guinea is: 1


The distribution of players for Cabo Verde is: 2.00%
The number of players in Cabo Verde is: 10


The distribution of players for Japan is: 1.40%
The number of players in Japan is: 7


The distribution of players for Spain is: 5.21

In [34]:
nation_df = df[df['league_name_id'] == 'eng1']
positions = ["ST", "RWB", "RW", "RM", "RB", "LWB", "LW", "LM", "LB", "GK", "CM", "CF", "CDM", "CB", "CAM"]
unique_nations = nation_df['nation_Nation'].unique()
unique_nations = list(unique_nations)

unique_regions = nation_df['nation_region'].unique()

total_count = nation_df.shape[0]
nation_count = nation_df['nation_Nation'].value_counts()

max_nation_name = nation_count.idxmax()
max_nation_num = nation_count.max()
print(f'The nation with the most players is: {max_nation_name} with {max_nation_num} players')


region_count = nation_df['nation_region'].value_counts()

max_region_name = region_count.idxmax()
max_region_num = region_count.max()
print(f'The region with the most players is: {max_region_name} with {max_region_num} players')

for region in unique_regions:
    region_spec_count = nation_df[nation_df['nation_region'] == region].shape[0]
    region_percentage_count = (region_spec_count / total_count) * 100
    print(f'The distribution of players for {region} is: {region_percentage_count:.2f}%')
    print(f'The number of players in {region} is: {region_spec_count}')

    for pos in positions:
        pos_df = nation_df[(nation_df[pos] == 1) & (nation_df['nation_region'] == region)]
        
        region_count_pos = pos_df.shape[0]
        region_min_age_pos = pos_df['nation_region'].value_counts().min()
        region_max_age_pos = pos_df['nation_region'].max()
        
        print(f'Number of players that are {pos} is :{region_count_pos:} from {region}')
        # print(f'Youngest age  for {pos} is : {min_age_pos:.2f} years old')
        # print(f'Oldest age for {pos} is : {max_age_pos:.2f} years old')
        #print(f'We are in this nation right now: {nation}')
        #print("\n")

print("\n")
print(f'The unique nations present in this league: {unique_regions}')
print("\n")
print(f'The total number of players in this league: {total_count}')


# for nation in unique_nations:
#     spec_count = nation_df[nation_df['nation_Nation'] == nation].shape[0]
#     percentage_count = (spec_count / total_count) * 100
#     print(f'The distribution of players for {nation} is: {percentage_count:.2f}%')
#     print(f'The number of players in {nation} is: {spec_count}')

#     for pos in positions:
#         pos_df = nation_df[(nation_df[pos] == 1) & (nation_df['nation_Nation'] == nation)]
        
#         count_pos = pos_df.shape[0]
#         min_age_pos = pos_df['nation_Nation'].value_counts().min()
#         max_age_pos = pos_df['nation_Nation'].max()
        
#         print(f'Number of players that are {pos} is :{count_pos:} from {nation}')
#         # print(f'Youngest age  for {pos} is : {min_age_pos:.2f} years old')
#         # print(f'Oldest age for {pos} is : {max_age_pos:.2f} years old')
#         #print(f'We are in this nation right now: {nation}')
#         #print("\n")

# print("\n")
# print(f'The unique nations present in this league: {unique_nations}')
# print("\n")
# print(f'The total number of players in this league: {total_count}')

The nation with the most players is: England with 241 players
The region with the most players is: Europe with 485 players
The distribution of players for Europe is: 76.50%
The number of players in Europe is: 485
Number of players that are ST is :67 from Europe
Number of players that are RWB is :19 from Europe
Number of players that are RW is :38 from Europe
Number of players that are RM is :39 from Europe
Number of players that are RB is :62 from Europe
Number of players that are LWB is :14 from Europe
Number of players that are LW is :42 from Europe
Number of players that are LM is :41 from Europe
Number of players that are LB is :58 from Europe
Number of players that are GK is :57 from Europe
Number of players that are CM is :116 from Europe
Number of players that are CF is :13 from Europe
Number of players that are CDM is :70 from Europe
Number of players that are CB is :113 from Europe
Number of players that are CAM is :61 from Europe
The distribution of players for Africa is: 8.2

In [21]:

nation_df = df[df['league_name_id'] == 'cyp1']


country_count = nation_df['nation_Nation'].value_counts()
max_c = nation_df['nation_Nation'].value_counts().max()
min_c = nation_df['nation_Nation'].value_counts().min()
nation_df['nation_Nation'].unique()

unique_nations = nation_df['nation_Nation'].unique()
unique_nations = list(unique_nations)
#print (unique_nations)

total_count = nation_df.shape[0]
print(total_count)
for nation in unique_nations:
    spec_count = nation_df[nation_df['nation_Nation'] == nation].shape[0]
    percentage_count = (spec_count / total_count) * 100
    print(f'the distribution for {nation} is: {percentage_count} %')


print(f'Total number of players by each country: {country_count}')
print(f'Max number players in a single country is: {max_c}')
print(f'Min number of players in a single country is: {min_c}')


positions = ["ST", "RWB", "RW", "RM", "RB", "LWB", "LW", "LM", "LB", "GK", "CM", "CF", "CDM", "CB", "CAM"]
print(f'Nation stats for each positions in the league: cyp1')
for pos in positions:
    pos_df = nation_df[nation_df[pos] == 1]

    if pos_df.empty:
        print(f'No players in this position: {pos}')
        print("\n")
    else:
        avg_age_pos = pos_df['nation_Nation'].value_counts().mean()
        min_age_pos = pos_df['nation_Nation'].value_counts().min()
        max_age_pos = pos_df['nation_Nation'].max()

        print(f'Average age for {pos} is : {avg_age_pos:.2f} years old')
        print(f'Youngest age  for {pos} is : {min_age_pos:.2f} years old')
        print(f'Oldest age for {pos} is : {max_age_pos:.2f} years old')
        print("\n")


27
the distribution for Portugal is: 7.4074074074074066 %
the distribution for Comoros is: 3.7037037037037033 %
the distribution for Slovenia is: 3.7037037037037033 %
the distribution for Serbia is: 3.7037037037037033 %
the distribution for Cyprus is: 29.629629629629626 %
the distribution for Angola is: 3.7037037037037033 %
the distribution for Congo DR is: 3.7037037037037033 %
the distribution for Argentina is: 3.7037037037037033 %
the distribution for Bosnia and Herzegovina is: 3.7037037037037033 %
the distribution for Morocco is: 3.7037037037037033 %
the distribution for Guinea-Bissau is: 3.7037037037037033 %
the distribution for Greece is: 3.7037037037037033 %
the distribution for Georgia is: 7.4074074074074066 %
the distribution for Bulgaria is: 3.7037037037037033 %
the distribution for Ghana is: 3.7037037037037033 %
the distribution for Brazil is: 7.4074074074074066 %
the distribution for Nigeria is: 3.7037037037037033 %
Total number of players by each country: nation_Nation
Cypr

ValueError: Unknown format code 'f' for object of type 'str'

In [68]:
for name in unique_leagues:
    #avg_age = df[df['league_name'] == name]['age'].mean()
    nations = df[df['league_name'] == name]['nation_Nation'].value_counts()
    print(f'Nation counts for {name} is : {nations}')

Nation counts for Primeira Liga (POR 1) [Portugal] is : nation_Nation
Portugal       203
Brazil         101
Spain           26
France          11
Cabo Verde      10
              ... 
Switzerland      1
Mexico           1
Scotland         1
Romania          1
Finland          1
Name: count, Length: 65, dtype: int64
Nation counts for League Two (ENG 4) [England] is : nation_Nation
England                  444
Republic of Ireland       58
Wales                     37
Scotland                  29
Northern Ireland          13
France                     7
Jamaica                    6
Gambia                     5
Grenada                    4
Cyprus                     2
New Zealand                2
Saint Kitts and Nevis      2
Guyana                     2
Nigeria                    2
Congo DR                   2
United States              2
Poland                     2
Kenya                      2
Montserrat                 2
Germany                    2
Australia                  2
Antigua 

## Some tips for analysis:

These are all per leauge:

- Get the highest value for the player attributes per league
- Get median values for player attributes
- Get minimum value for player attributes
- Do preferred foot and do it by position too, maybe LW hav e preference for left footed, outswinging or right footed, to cut inside.
- If you have time, do clubs for the different leagues. (This one may be too much maybe put it in the recommendation for extension and continuation)
- Do the same analysis as above, but do it by position so (e.g. highest sprint speed for RW)
- Get number of players with preferred foot, see if it helps identify anything
- Maybe see if correlation between preferred foot and the position (LW has more number of preferred_foot == left than right)
- Get longest career length in league (See if people who had long careers are in this league)
- Get shortest career lenght (most likely 1 year)
- Get average career length (This could maybe indicate if the league is for newer players or more established players)
- Get the number of the career lengths for all ofthe 3 categories above. And a distribution of them, we can see if th eleague is more geared towards almost retiring players or newer players.
- Do positions by career length, see if their is a correlatiion between experience and the positions being played.
- Do age and nationalitty, see if some nationalities have younger players in the league or if its older players by country
- 

### Feel free to think up and add more to make the analysis better

In [111]:

player_attributes = [
    "height_cm",
    "weight_kg",
    "crossing",
    "finishing",
    "heading_accuracy",
    "short_passing",
    "volleys",
    "dribbling",
    "curve",
    "fk_accuracy",
    "long_passing",
    "ball_control",
    "acceleration",
    "sprint_speed",
    "agility",
    "reactions",
    "balance",
    "shot_power",
    "jumping",
    "stamina",
    "strength",
    "long_shots",
    "aggression",
    "interceptions",
    "positioning",
    "vision",
    "penalties",
    "composure",
    "defensive_awareness",
    "standing_tackle",
    "sliding_tackle",
    "gk_diving",
    "gk_handling",
    "gk_kicking",
    "gk_positioning",
    "gk_reflexes",
    "age"
]

positions = ["ST", "RWB", "RW", "RM", "RB", "LWB", "LW", "LM", "LB", "GK", "CM", "CF", "CDM", "CB", "CAM"]

for name in unique_leagues_id:
    final_df = df[df['league_name_id'] == name]
    attr_max = {}
    attr_min = {}
    attr_avg = {}
    
    
    
    
    left_df = final_df[final_df['preferred_foot_Left'] == 1]
    right_df = final_df[final_df['preferred_foot_Right'] == 1]
    
    count_left_total = left_df.shape[0]
    count_right_total = right_df.shape[0]
    
    total_ovr = count_left_total + count_right_total
    
    print(f'Total Number of players in {name} are: {total_ovr}')
    print(f'Total Number of left footed players {name} are: {count_left_total}')
    print(f'Total Number of right footed players  {name} are: {count_right_total}')
    
    
    for attr in player_attributes:
        total_attr_max = final_df[attr].max()
        total_attr_min = final_df[attr].min()
        total_attr_avg = final_df[attr].mean()
        print (f'The Overall maximum {attr} is: {total_attr_max}')
        print (f'The Overall minimum {attr} is: {total_attr_min}')
        print (f'The Overall average {attr} is: {total_attr_avg}')
        print("\n")
    
    
    for pos in positions:
        pos_df = final_df[final_df[pos] == 1]
    
        if pos_df.empty:
            print(f'There are no {pos}!')
        else:
    
            left_df = pos_df[pos_df['preferred_foot_Left'] == 1]
            right_df = pos_df[pos_df['preferred_foot_Right'] == 1]
    
            count_left = left_df.shape[0]
            count_right = right_df.shape[0]
            pos_total = count_left + count_right
    
    
            
            
            if abs(count_left - count_right) < 5 or abs(count_left - count_right) < (0.10 * pos_total):
                print(f'Not really a better chance if you are left footed or right footed as a {pos} in {name}')
                #foot_score = 1  
            else:
                
                if count_left > count_right:
                    print(f'Better chance if you are left footed as a {pos} in {name}')
                    #foot_score = 1 if player_foot == 'Left' else 0.5
                else:
                    print(f'Better chance if you are right footed as a {pos} in {name}')
                    #foot_score = 1 if player_foot == 'Right' else 0.5
        
    
    
    
    
            print("\n")
    
    
            
            print(f'Number of left footed players that are {pos}: {count_left}')
            print(f'Number of right footed players that are {pos}: {count_right}')
            
            if pos not in attr_max:
                attr_max[pos] = {}
                attr_min[pos] = {}
                attr_avg[pos] = {}
            for attr in player_attributes:
                attr_max[pos][attr] = pos_df[attr].max()
                attr_min[pos][attr] = pos_df[attr].min()
                attr_avg[pos][attr] = pos_df[attr].mean()
                print (f'The maximum {attr} for {pos} is: {attr_max[pos][attr]}')
                print (f'The minimum {attr} for {pos} is: {attr_min[pos][attr]}')
                print (f'The average {attr} for {pos} is: {attr_avg[pos][attr]}')
                print("\n")
    
        print("\n")


Total Number of players in por1 are: 499
Total Number of left footed players por1 are: 133
Total Number of right footed players  por1 are: 366
The Overall maximum height_cm is: 199
The Overall minimum height_cm is: 164
The Overall average height_cm is: 182.2064128256513


The Overall maximum weight_kg is: 95
The Overall minimum weight_kg is: 54
The Overall average weight_kg is: 75.5250501002004


The Overall maximum crossing is: 84
The Overall minimum crossing is: 9
The Overall average crossing is: 50.4188376753507


The Overall maximum finishing is: 85
The Overall minimum finishing is: 4
The Overall average finishing is: 46.99799599198397


The Overall maximum heading_accuracy is: 84
The Overall minimum heading_accuracy is: 10
The Overall average heading_accuracy is: 51.69539078156313


The Overall maximum short_passing is: 87
The Overall minimum short_passing is: 14
The Overall average short_passing is: 60.62725450901804


The Overall maximum volleys is: 84
The Overall minimum volley

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



# WHEN TALKING ABOUT CONTINUING AND EXTENDING THE PROJECT AFTERWARDS, LIKE THE RECOMMENDATION SOME MAJOR POINTS ARE BELOW:

- GET MORE DIVERSE DATA, SUCH AS A DATA SET WITH MORE CF, CAM ADN LW FOR THE POSITIONS WHICH ARE UNDER REPRESENTED.
- GET DATA WHICH HAS MORE GENERAL PURPOSE SO ATTRIBUTES FOR NORMAL PEOPLE SO THE MODEL IS BETTER AT PREDICTING THEM. SINCE RIGHT NOW IT IS ONLY PROFESSIONAL PLAYERS.
- GET MORE DIVERSE DATA FROM LEAGUES AS RIGHT NOW THERE IS MANY LEAGUES BUT FOR THE LOWER LEAGUES THERE IS ONLY 1 OR 2 TEAMS PER THOSE LEAGUES.
- WE KNOW THE PLAYER ATTRIBUTES WERE SOURCED USING STATISTICAL DATA OF REAL PLAYER PERFORMANCES AND THEN CONVERTED IN NUMERICAL VALUES BY EA. THEY USED OPTA, HOWVER THERE IS NO REAL WAY IN WHICH WE CAN TELL WHAT WAS THE STANDARD FOR THOSE VALUES. E.G- IF SPRINT SPEED WAS A 100M DASH, TOP SPEED OVER THE LEAGUE SEASON, TOP SPEED IN COMPARISON TO OTHER PLAYERS IN THE SAME LEAGUE? SO A GOAL WOULD BE STANDARDIZE AND IDENTFIY THE WAY IN WHICH THOSE VALUES WERE DETERMINED TO THEN ALLOW THE USER THE KNOWLEDGE SO THAT THEY CAN MAKE A MORE INFORMED DECISION.
- EXTEND THE APPLICATION TO WOMEN ATHLETS IN FOOTBALL, AS WELL AS YOUTH TEAMS AS THEY WERE NOT PART OF THIS.
- EXTEND THE APPLICATION TO OTHER SPORTS WITH VALUES ADN METRIC SPECIFIC TO THEM.
- DO FURTHER AND DEEPER ANALYSIS INTO MAYBE THE CLUBS FOR EACH LEAGUE, TO SEE DEEPER UNDERLYING TRENDS AND PLACEMENT OPPORTUNITIES.

In [62]:
nav_name = df[df['league_name_id'] == 'ukr1']['nation_Nation'].unique()
nav_name = str(nav_name)
print(nav_name)

['Brazil' 'Ukraine' 'Burkina Faso' 'Nigeria' 'Tanzania' 'Georgia'
 'Senegal' 'Israel']


In [70]:
df[df['league_name_id'] == 'ukr1']['RWB'].value_counts()

RWB
0    56
Name: count, dtype: int64

In [72]:
unique_leagues

array(['Primeira Liga (POR 1) [Portugal]', 'League Two (ENG 4) [England]',
       'Pro League (SAU 1) [Saudi Arabia]',
       'Allsvenskan (SWE 1) [Sweden]', 'La Liga (ESP 1) [Spain]',
       'Primera División (PAR 1) [Paraguay]', 'Ligue 1 (FRA 1) [France]',
       'Premiership (SP 1) [Scotland]', 'Liga Pro (ECU 1) [Ecuador]',
       'División de Fútbol Profesional (BOL 1) [Bolivia]',
       'Primera División (URY 1) [Uruguay]',
       'Eliteserien (NOR 1) [Norway]',
       'Liga Profesional de Fútbol (ARG 1) [Argentina]',
       'Major League Soccer (MLS 1) [USA]',
       '2. Bundesliga (GER 2) [Germany]', 'Bundesliga (GER 1) [Germany]',
       'Primera Division (VEN 1) [Venezuela]',
       'Eredivisie (NED 1) [Netherlands]', 'Süper Lig (TUR 1) [Turkey]',
       'Ligue 2 (FRA 2) [France]', 'Championship (ENG 2) [England]',
       'La Liga 2 (ESP 2) [Spain]', 'Premier League (ENG 1) [England]',
       'Serie A (ITA 1) [Italy]', 'A-League Men (AUS 1) [Australia]',
       'Serie B (ITA 2

In [210]:
df['nation_Nation'].unique()

array(['Portugal', 'England', 'Sweden', 'Spain', 'Paraguay', 'France',
       'Republic of Ireland', 'Scotland', 'Ecuador', 'Argentina',
       'Bolivia', 'Uruguay', 'Norway', 'Brazil', 'United States',
       'Czechia', 'Germany', 'Guinea-Bissau', 'Venezuela', 'Denmark',
       'Türkiye', 'Comoros', 'Wales', 'Netherlands', 'Guinea', 'Zambia',
       'Australia', 'Poland', 'Romania', 'Ghana', 'Gabon', 'Gambia',
       'Finland', 'Costa Rica', 'Moldova', 'Japan', 'Italy', 'Grenada',
       'Congo', 'Belgium', 'Georgia', 'Serbia', 'Canada',
       'Trinidad and Tobago', 'Morocco', 'Northern Ireland', 'Kosovo',
       'Angola', "Côte d'Ivoire", 'Burkina Faso', 'Cabo Verde',
       'Switzerland', 'Iceland', 'Mali', 'Nigeria', 'Chile', 'Senegal',
       'Indonesia', 'Sierra Leone', 'Colombia', 'Peru', 'Estonia',
       'Dominican Republic', 'Austria', 'Cameroon', 'Congo DR', 'Croatia',
       'Cyprus', 'North Macedonia', 'Saudi Arabia', 'India', 'Panama',
       'Slovakia', 'Korea Republic'

In [34]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 18608 entries, 0 to 18607
Data columns (total 96 columns):
 #   Column                        Non-Null Count  Dtype   
---  ------                        --------------  -----   
 0   Unnamed: 0.1                  18608 non-null  int64   
 1   Unnamed: 0                    18608 non-null  int64   
 2   player_id                     18608 non-null  int64   
 3   name                          18608 non-null  object  
 4   full_name                     18608 non-null  object  
 5   height_cm                     18608 non-null  int64   
 6   weight_kg                     18608 non-null  int64   
 7   dob                           18608 non-null  object  
 8   positions                     18608 non-null  object  
 9   preferred_foot                18608 non-null  object  
 10  body_type                     18608 non-null  object  
 11  club_id                       18608 non-null  int64   
 12  club_name                     18608 non-null  

In [36]:
df['league_Career_length'].isnull().sum()

3848

In [38]:
df['league_Career_length'] = df['league_Career_length'].fillna(1)

In [40]:
df['league_Start_year_final'] = df['league_Start_year_final'].fillna(2023)
df['league_End/Recent_year_final'] = df['league_End/Recent_year_final'].fillna(2024)

In [42]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 18608 entries, 0 to 18607
Data columns (total 96 columns):
 #   Column                        Non-Null Count  Dtype   
---  ------                        --------------  -----   
 0   Unnamed: 0.1                  18608 non-null  int64   
 1   Unnamed: 0                    18608 non-null  int64   
 2   player_id                     18608 non-null  int64   
 3   name                          18608 non-null  object  
 4   full_name                     18608 non-null  object  
 5   height_cm                     18608 non-null  int64   
 6   weight_kg                     18608 non-null  int64   
 7   dob                           18608 non-null  object  
 8   positions                     18608 non-null  object  
 9   preferred_foot                18608 non-null  object  
 10  body_type                     18608 non-null  object  
 11  club_id                       18608 non-null  int64   
 12  club_name                     18608 non-null  

In [44]:
df.to_csv('Final_project_finished_4.csv', index=False)  # index=False avoids saving row indices

In [45]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 18608 entries, 0 to 18607
Data columns (total 96 columns):
 #   Column                        Non-Null Count  Dtype   
---  ------                        --------------  -----   
 0   Unnamed: 0.1                  18608 non-null  int64   
 1   Unnamed: 0                    18608 non-null  int64   
 2   player_id                     18608 non-null  int64   
 3   name                          18608 non-null  object  
 4   full_name                     18608 non-null  object  
 5   height_cm                     18608 non-null  int64   
 6   weight_kg                     18608 non-null  int64   
 7   dob                           18608 non-null  object  
 8   positions                     18608 non-null  object  
 9   preferred_foot                18608 non-null  object  
 10  body_type                     18608 non-null  object  
 11  club_id                       18608 non-null  int64   
 12  club_name                     18608 non-null  

In [213]:
df['nation_Nation'].unique()

array(['Portugal', 'England', 'Sweden', 'Spain', 'Paraguay', 'France',
       'Republic of Ireland', 'Scotland', 'Ecuador', 'Argentina',
       'Bolivia', 'Uruguay', 'Norway', 'Brazil', 'United States',
       'Czechia', 'Germany', 'Guinea-Bissau', 'Venezuela', 'Denmark',
       'Türkiye', 'Comoros', 'Wales', 'Netherlands', 'Guinea', 'Zambia',
       'Australia', 'Poland', 'Romania', 'Ghana', 'Gabon', 'Gambia',
       'Finland', 'Costa Rica', 'Moldova', 'Japan', 'Italy', 'Grenada',
       'Congo', 'Belgium', 'Georgia', 'Serbia', 'Canada',
       'Trinidad and Tobago', 'Morocco', 'Northern Ireland', 'Kosovo',
       'Angola', "Côte d'Ivoire", 'Burkina Faso', 'Cabo Verde',
       'Switzerland', 'Iceland', 'Mali', 'Nigeria', 'Chile', 'Senegal',
       'Indonesia', 'Sierra Leone', 'Colombia', 'Peru', 'Estonia',
       'Dominican Republic', 'Austria', 'Cameroon', 'Congo DR', 'Croatia',
       'Cyprus', 'North Macedonia', 'Saudi Arabia', 'India', 'Panama',
       'Slovakia', 'Korea Republic'

# Mapping countires to regions/ Continents

In [215]:
continent_map = {
    # Countries in Europe 47
    'Portugal': 'Europe', #
    'England': 'Europe',#
    'Sweden': 'Europe',#
    'Spain': 'Europe',#
    'France': 'Europe',#
    'Republic of Ireland': 'Europe',#
    'Scotland': 'Europe',#
    'Norway': 'Europe',#
    'Czechia': 'Europe',#
    'Germany': 'Europe',#
    'Denmark': 'Europe',#
    'Wales': 'Europe',#
    'Netherlands': 'Europe',#
    'Poland': 'Europe',#
    'Romania': 'Europe',#
    'Finland': 'Europe',#
    'Moldova': 'Europe',#
    'Italy': 'Europe',#
    'Belgium': 'Europe',#
    'Georgia': 'Europe',#
    'Serbia': 'Europe',#
    'Northern Ireland': 'Europe',#
    'Kosovo': 'Europe',#
    'Switzerland': 'Europe',#
    'Iceland': 'Europe',#
    'Austria': 'Europe',#
    'Estonia': 'Europe',#
    'Croatia': 'Europe',#
    'Cyprus': 'Europe',#
    'North Macedonia': 'Europe',#
    'Slovakia': 'Europe',#
    'Greece': 'Europe',#
    'Belarus': 'Europe',#
    'Bulgaria': 'Europe',#
    'Lithuania': 'Europe',#
    'Ukraine': 'Europe', #
    'Albania': 'Europe',#
    'Azerbaijan': 'Europe',#
    'Montenegro': 'Europe',#
    'Luxembourg': 'Europe',#
    'Slovenia': 'Europe',#
    'Hungary': 'Europe',#
    'Russia': 'Europe', #
    'Andorra': 'Europe', #
    'Faroe Islands': 'Europe', #
    'Malta': 'Europe',#
    'San Marino': 'Europe',
    'Latvia': 'Europe',#

    # Africa pre 47, 
    'Guinea-Bissau': 'Africa',#
    'Comoros': 'Africa',#
    'Guinea': 'Africa', #
    'Zambia': 'Africa',#
    'Ghana': 'Africa',#
    'Gabon': 'Africa',#
    'Gambia': 'Africa',#
    'Congo': 'Africa',#
    'Morocco': 'Africa', #
    'Angola': 'Africa',#
    "Côte d'Ivoire": 'Africa',#
    'Burkina Faso': 'Africa',#
    'Cabo Verde': 'Africa', #
    'Mali': 'Africa',#
    'Nigeria': 'Africa',#
    'Senegal': 'Africa',#
    'Sierra Leone': 'Africa',#
    'Cameroon': 'Africa', #
    'Congo DR': 'Africa',#
    'Algeria': 'Africa',#
    'Zimbabwe': 'Africa',#
    'Equatorial Guinea': 'Africa',#
    'Tunisia': 'Africa',#
    'Egypt': 'Africa',#
    'Liberia': 'Africa', #
    'Togo': 'Africa',#
    'Palestine': 'Africa',#
    'Madagascar': 'Africa',#
    'Uganda': 'Africa',#
    'Benin': 'Africa',#
    'Namibia': 'Africa',#
    'Mauritania': 'Africa',#
    'Mozambique': 'Africa', #
    'Sudan': 'Africa', #
    'Somalia': 'Africa',#
    'Rwanda': 'Africa',#
    'Chad': 'Africa',#
    'Malawi': 'Africa', #
    'Burundi': 'Africa', #
    'South Sudan': 'Africa',#
    'South Africa': 'Africa',#
    'Kenya': 'Africa',#
    'Libya': 'Africa',#
    'Tanzania': 'Africa',#

    # Asia pre 87
    'Türkiye' :'Asia',#
    'Japan': 'Asia', #
    'Indonesia': 'Asia', #
    'Saudi Arabia': 'Asia', #
    'India': 'Asia',#
    'Korea Republic': 'Asia', #
    'Syria': 'Asia', #
    'Uzbekistan': 'Asia', #
    'Iraq': 'Asia',#
    'China PR': 'Asia',#
    'Hong Kong': 'Asia', #
    'Israel': 'Asia',#
    'Philippines': 'Asia',#
    'Sri Lanka': 'Asia',#
    'Iran': 'Asia',#
    'Jordan': 'Asia', #
    'Bangladesh': 'Asia',#
    'Thailand': 'Asia',#
    'Pakistan': 'Asia',#
    'Lebanon': 'Asia', #
    'Bahrain': 'Asia',#
    'Kyrgyz Republic': 'Asia',#
    'United Arab Emirates': 'Asia', #
    'Chinese Taipei': 'Asia',#
    'Nepal': 'Asia',#
    'Kazakhstan': 'Asia',#

    # North America pre 111
    'United States': 'North America',#
    'Canada': 'North America', #
    'Mexico': 'North America',#

    # Central America & Caribbean (can be merged with North America) pre 115
    'Costa Rica': 'Central America',#
    'Trinidad and Tobago': 'Central America',#
    'Panama': 'Central America',#
    'Haiti': 'Central America',#
    'Curacao': 'Central America',#
    'Dominican Republic': 'Central America', #
    'Jamaica': 'Central America',#
    'Saint Kitts and Nevis': 'Central America',#
    'Guatemala': 'Central America',#
    'Cuba': 'Central America', #
    'El Salvador': 'Central America', #
    'Puerto Rico': 'Central America',#
    'Honduras': 'Central America',#
    'Saint Lucia': 'Central America',#
    'Antigua and Barbuda': 'Central America',#
    'Barbados': 'Central America', #
    'Grenada': 'Central America',#
    'Montserrat': 'Central America',#

    # South America $133
    'Paraguay': 'South America', #
    'Ecuador': 'South America',#
    'Argentina': 'South America',#
    'Bolivia': 'South America',#
    'Uruguay': 'South America', #
    'Brazil': 'South America',#
    'Venezuela': 'South America',#
    'Chile': 'South America', #
    'Colombia': 'South America',#
    'Peru': 'South America', #
    'Suriname': 'South America',#
    'Guyana': 'South America',#

    # Oceania #145
    'Australia': 'Oceania',#
    'New Zealand': 'Oceania', #
    'Fiji': 'Oceania',#
    'Vanuatu': 'Oceania',#
    'New Caledonia': 'Oceania',#

    # Other/Unknown pre 150
    'São Tomé and Príncipe': 'Africa',  #
    'Armenia': 'Europe',  #
    'Bosnia and Herzegovina': 'Europe',#
    'Central African Republic': 'Africa',#
    'Bermuda': 'Other',#
    'Greenland': 'Other',#
}

In [217]:
df['nation_region'] = df['nation_Nation'].map(continent_map)

In [219]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 18608 entries, 0 to 18607
Data columns (total 98 columns):
 #   Column                        Non-Null Count  Dtype   
---  ------                        --------------  -----   
 0   Unnamed: 0.1                  18608 non-null  int64   
 1   Unnamed: 0                    18608 non-null  int64   
 2   player_id                     18608 non-null  int64   
 3   name                          18608 non-null  object  
 4   full_name                     18608 non-null  object  
 5   height_cm                     18608 non-null  int64   
 6   weight_kg                     18608 non-null  int64   
 7   dob                           18608 non-null  object  
 8   positions                     18608 non-null  object  
 9   preferred_foot                18608 non-null  object  
 10  body_type                     18608 non-null  object  
 11  club_id                       18608 non-null  int64   
 12  club_name                     18608 non-null  

In [221]:
df.to_csv('Final_project_finished_Continents.csv', index=False)  # index=False avoids saving row indices

In [229]:
df[df['league_name_id'] == 'cyp1']['league_Career_length']

4.703703703703703

In [233]:
test_df = df[df['league_name_id'] == 'cyp1']

In [243]:
test_df[test_df['ST'] == 1]['age']

1040    32
1353    35
2055    34
5552    28
7332    31
Name: age, dtype: int64

In [115]:
df['nation_region'].unique()

array(['Europe', 'South America', 'North America', 'Africa', 'Asia',
       'Oceania', 'Central America', 'Other'], dtype=object)